In [232]:
from bs4 import BeautifulSoup
import requests
from bs4.element import Comment
import re
from nltk.tokenize import word_tokenize
import csv
import json
from sklearn.feature_extraction.text import TfidfVectorizer
import numpy as np
import pickle


In [2]:
base_url = 'https://en.wikipedia.org'

In [3]:
# Get the links in the paragraphs for wikipedia URL
def get_links_for_url(url):
    url_title = url[url.rfind('wiki')+5:]
    print("reading page: " + url_title)
    page = requests.get(url)
    try:
        soup = BeautifulSoup(page.text, "html5lib")
        tags = soup.find_all('p')
        res_links = []
        for tag in tags:
            links = tag.find_all('a', attrs={'href': re.compile("^/wiki/")})
            for link in links:
                res_links.append(link.get('href'))
        return res_links
    except Exception as e:
        print("Error loading page")
        return None
        

In [4]:
# Get cleaned text in the paragraph for wikipedia URL
def get_text_for_url(url):
    url_title = url[url.rfind('wiki')+5:]
    print("reading page: " + url_title)
    page = requests.get(url)
    try:
        soup = BeautifulSoup(page.text, "html5lib")
        text = soup.find_all('p')
        full_text = ""
        num = 0
        for t in text:
            if num > 5:
                break
            if not t.find('img') and (t.name == 'p' or t.name == 'ul'):
                text = str(t.getText().replace('\n', ''))
                full_text += re.sub("[\(\[].*?[\)\]]", "", text) + " "
                num += 1
        return full_text
    except Exception as e:
        print("Error loading page")
        return None

In [5]:
links = get_links_for_url(base_url + '/wiki/Computer_science')
links

reading page: Computer_science


['/wiki/Process_(engineering)',
 '/wiki/Data',
 '/wiki/Computer_program',
 '/wiki/Algorithm',
 '/wiki/Data_processing',
 '/wiki/Data_storage',
 '/wiki/Communication',
 '/wiki/Digital_data',
 '/wiki/Information',
 '/wiki/Computer_scientist',
 '/wiki/Theory_of_computation',
 '/wiki/Software_design',
 '/wiki/Software_system',
 '/wiki/Practical_disciplines',
 '/wiki/Computational_complexity_theory',
 '/wiki/Computer_graphics_(computer_science)',
 '/wiki/Programming_language_theory',
 '/wiki/Computer_programming',
 '/wiki/Programming_language',
 '/wiki/Complex_systems',
 '/wiki/Human%E2%80%93computer_interaction',
 '/wiki/Computer_accessibility',
 '/wiki/Digital_computer',
 '/wiki/Abacus',
 '/wiki/Algorithm',
 '/wiki/Wilhelm_Schickard',
 '/wiki/Mechanical_calculator',
 '/wiki/Gottfried_Leibniz',
 '/wiki/Stepped_Reckoner',
 '/wiki/Charles_Xavier_Thomas',
 '/wiki/Mechanical_calculator',
 '/wiki/Arithmometer',
 '/wiki/Charles_Babbage',
 '/wiki/Difference_Engine',
 '/wiki/Analytical_Engine',
 '

In [6]:
text = get_text_for_url(base_url + '/wiki/Computer_science')
text

reading page: Computer_science


' Computer science is the study of processes that interact with data and that can be represented as data in the form of programs. It enables the use of algorithms to manipulate, store, and communicate digital information. A computer scientist studies the theory of computation and the practice of designing software systems. Its fields can be divided into theoretical and practical disciplines. Computational complexity theory is highly abstract, while computer graphics emphasizes real-world applications. Programming language theory considers approaches to the description of computational processes, while computer programming itself involves the use of programming languages and complex systems. Human–computer interaction considers the challenges in making computers useful, usable, and accessible. The earliest foundations of what would become computer science predate the invention of the modern digital computer. Machines for calculating fixed numerical tasks such as the abacus have existed 

In [141]:
def reduce(u, v):
    return (u[0].union(v[0]), u[1] + v[1])

def clean_text(text):
    if text is None:
        return None
    regex = re.compile('[^a-zA-Z ]')
    text = regex.sub('', text)
    tokenized_text = word_tokenize(text.lower())
    return tokenized_text


def clean_text_for_vectorizer(text):
    if text is None:
        return None
    regex = re.compile('[^a-zA-Z ]')
    text = regex.sub('', text)
    return text.lower()


In [221]:
def generate_representation_for_course_description(course_description, branching_factor, search_depth, representation):
    '''
    course_description: [str], string of text description for a course
    branching_factor: float, in range(0, 1), what percentage of the links we want to traverse at each step
    search_depth: the maximum depth of link traversals starting from an original word in the course_description
    
    Returns: (links, representation)
    '''
    course_description
    res = (set(), "")
    explored_urls = set()
    for word in course_description:
        url = '/wiki/' + word
        res = reduce(res, generate_representation_for_word(explored_urls, url, branching_factor, search_depth, ""))
    return res
    
    

def generate_representation_for_word(explored_urls, url, branching_factor, search_depth, representation):
    '''
    explored_urls: set, of urls that have already been explored
    url: the url we wish to find the wikipedia article on, 
    if word is multiple words, it will appear as /wiki/computer_science, /wiki/computer_graphics, etc
    branching_factor: float, in range(0, 1), which percentage of the links we want to traverse at each step
    search_depth: int, the maximum depth of link traversals starting from word
    
    return: (links, represenation)
    links: list of strings
    representation: string
    '''
    if search_depth == 0 or url in explored_urls:
        return (set(), "")
    explored_urls.add(url)
    links = get_links_for_url(base_url + url)
    if links is None: # Only if the url is not valid
        return (explored_urls, representation)
    text = get_text_for_url(base_url + url)
    representation += " " + text
    next_links = links[:min(8, int(branching_factor * len(links)))]
    
    res = (explored_urls, representation)
    for link in next_links:
        res = reduce(res, generate_representation_for_word(explored_urls, link, branching_factor, search_depth - 1, ""))
        
    return res

In [215]:
rep_for_cs_course = generate_representation_for_course_description(["Computer_science", "biology"], 0.05, 2, "")

reading page: Computer_science
reading page: Computer_science
reading page: Process_(engineering)
reading page: Process_(engineering)
reading page: Data
reading page: Data
reading page: Computer_program
reading page: Computer_program
reading page: Algorithm
reading page: Algorithm
reading page: Data_processing
reading page: Data_processing
reading page: Data_storage
reading page: Data_storage
reading page: Communication
reading page: Communication
reading page: Digital_data
reading page: Digital_data
reading page: biology
reading page: biology
reading page: Natural_science
reading page: Natural_science
reading page: Life
reading page: Life
reading page: Organism
reading page: Organism
reading page: Anatomy
reading page: Anatomy
reading page: Biochemistry
reading page: Biochemistry
reading page: Molecular_biology
reading page: Molecular_biology
reading page: Physiology
reading page: Physiology
reading page: Developmental_biology
reading page: Developmental_biology


In [216]:
rep_for_cs_course

({'/wiki/Algorithm',
  '/wiki/Anatomy',
  '/wiki/Biochemistry',
  '/wiki/Communication',
  '/wiki/Computer_program',
  '/wiki/Computer_science',
  '/wiki/Data',
  '/wiki/Data_processing',
  '/wiki/Data_storage',
  '/wiki/Developmental_biology',
  '/wiki/Digital_data',
  '/wiki/Life',
  '/wiki/Molecular_biology',
  '/wiki/Natural_science',
  '/wiki/Organism',
  '/wiki/Physiology',
  '/wiki/Process_(engineering)',
  '/wiki/biology'},
 '  Computer science is the study of processes that interact with data and that can be represented as data in the form of programs. It enables the use of algorithms to manipulate, store, and communicate digital information. A computer scientist studies the theory of computation and the practice of designing software systems. Its fields can be divided into theoretical and practical disciplines. Computational complexity theory is highly abstract, while computer graphics emphasizes real-world applications. Programming language theory considers approaches to the

In [73]:
#rep_for_Computer_science = generate_representation_for_word(set(), '/wiki/Computer_science', 0.05, 2, "")
# rep_for_Computer_science

In [217]:
with open("./data/courseroster/full_json.txt") as f:
    cornell_course_descriptions = json.load(f)

In [218]:
cornell_course_descriptions.keys()

dict_keys(['VIEN', 'BSOC', 'PLPPM', 'FREN', 'GREEK', 'PMA', 'AIIS', 'KOREA', 'NCC', 'CHEM', 'TURK', 'TAMIL', 'YORUB', 'MAE', 'BENGL', 'PLBIO', 'VISST', 'COMM', 'MEDVL', 'ECON', 'ENMGT', 'CHIN', 'HIST', 'PERSN', 'PUNJB', 'ORIE', 'NEPAL', 'ILRLR', 'URDU', 'BEE', 'EDUC', 'ENGRI', 'WOLOF', 'BIOG', 'HD', 'INFO', 'PSYCH', 'ENGRD', 'ARAB', 'STSCI', 'SNLIT', 'PHYS', 'PORT', 'RELST', 'ALS', 'FSAD', 'PLSCS', 'COGST', 'CZECH', 'MATH', 'NBA', 'PLHRT', 'ENTOM', 'GERST', 'JWST', 'ILRLE', 'TIBET', 'MSE', 'VETMI', 'IARD', 'PADM', 'ECE', 'BIOMI', 'TOX', 'AKKAD', 'SINHA', 'ARKEO', 'NTRES', 'SPAN', 'COLLS', 'KHMER', 'AMST', 'AEM', 'JPLIT', 'CHLIT', 'HEBRW', 'BIOMS', 'PLSCI', 'ROMS', 'ROMAN', 'PHIL', 'BIONB', 'ASTRO', 'FGSS', 'DSOC', 'BIOEE', 'ILRHR', 'VETMM', 'CAPS', 'PE', 'NACCT', 'AAS', 'ASRC', 'STS', 'JAPAN', 'MOGRK', 'KANAD', 'AIRS', 'ILROB', 'ENGRC', 'ENGL', 'HINDI', 'VTPMD', 'TECH', 'ILRIC', 'LATIN', 'SWAHL', 'BME', 'VTBMS', 'ART', 'NS', 'HADM', 'ENGRG', 'VTMED', 'ZULU', 'GRAD', 'ANSC', 'LA', 'COML

In [219]:
cornell_course_descriptions['CS'][0]

{'courseNumber': '1110',
 'courseTitle': 'Introduction to Computing Using Python',
 'description': 'Programming and problem solving using Python. Emphasizes principles of software development, style, and testing. Topics include procedures and functions, iteration, recusion, arrays and vectors, strings, an operational model of procedure and function calls, algorithms, exceptions, object-oriented programming, and GUIs (graphical user interfaces). Weekly labs provide guided practice on the computer, with staff present to help. Assignments use graphics and GUIs to help develop fluency and understanding.',
 'offered': 'Fall, Spring, Summer.',
 'outcomes': ' Be fluent in the use of procedural statements -assignments, conditional statements, loops, method calls- and  arrays. Be able to design, code, and test small Python programs that meet requirements expressed in English. This includes a basic understanding of top-down design. Understand the concepts of object-oriented programming as used i

In [207]:
corpus = []
all_major_courses = [cornell_course_descriptions[key] for key in cornell_course_descriptions.keys()]
all_courses = []
for major_courses in all_major_courses:
    all_courses += major_courses

for course_data in all_courses:
    course_number = course_data['courseNumber']
    course_title = course_data['courseTitle']
    course_desc = course_data['description']
    cleaned_course_desc = clean_text_for_vectorizer(course_desc)
    if cleaned_course_desc != None and cleaned_course_desc != []: 
        corpus.append(cleaned_course_desc)
    course_outcome = None
    try:
        course_outcome = course_data['outcome']
    except Exception as e:
        course_outcome = ""

In [208]:
print(len(corpus))
print(corpus[4000])

4089
some of our very best evidence for roman art survives in the form of frescoes in rome ostia and the bay of naples exploring imperial palaces rural villas town houses shops baths tombs taverns and gardens we will examine the visual dynamics and sociocultural significance of wallpaintings within their original archaeological contexts the study of frescoes offers an exciting means of tackling important questions relating to roman social history alongside the complexities of representation within the grecoroman visual tradition including the relationship between art and nature the use of myth the spatial dynamics of interior decorative schemes visualverbal relations and concepts of ornament medium and abstraction this course will be taught as a traveling seminar which will include a trip to rome and bay of naples over spring break spaces are limited


In [209]:
vectorizer = TfidfVectorizer(lowercase= True, preprocessor=lambda x: x, stop_words='english', max_df=0.8, min_df = 2,smooth_idf=True)
X = vectorizer.fit_transform(corpus)
doc_by_vocab = vectorizer.fit_transform([d for d in corpus]).toarray()

In [223]:
def get_top_n_tfidf_terms_from_text(vectorizer, text, n):
    print("S")
    if text is None:
        return []
    feature_array = np.array(vectorizer.get_feature_names())
    transformed_text = vectorizer.transform([text])
    tfidf_sorting = np.argsort(transformed_text.toarray()).flatten()[::-1]
    k = len(text.split())
    top_n = feature_array[tfidf_sorting][:min(k, n)]
    return top_n

def get_top_n_important_terms_from_text(vectorizer, text, n):
    pass
    

In [225]:
cs4110 = "Introduction to the design of systems programs, with emphasis on multiprogrammed operating systems. Topics include concurrency, synchronization, deadlocks, memory management, protection, input-output methods, networking, file systems and security. The impact of network and distributed computing environments on operating systems is also discussed."
print(get_top_n_tfidf_terms_from_text(vectorizer, clean_text_for_vectorizer(cs4110), 5))

S
['systems' 'operating' 'file' 'concurrency' 'inputoutput']


In [227]:
course_representations = {}
for course_data in cornell_course_descriptions['CS']:
    course_number = course_data['courseNumber']
    course_desc = course_data['description']
    cleaned_course_desc = clean_text_for_vectorizer(course_desc)
    print(course_number)
    print(course_desc)
    print(cleaned_course_desc)
    top_tfidf_words = get_top_n_tfidf_terms_from_text(vectorizer, cleaned_course_desc, 10)
    print(top_tfidf_words)
    course_representation = generate_representation_for_course_description(top_tfidf_words, 0.10, 2, "")
    course_representations['CS '+str(course_number)] = course_representation
    print(course_representation)
    print("************************")

1110
Programming and problem solving using Python. Emphasizes principles of software development, style, and testing. Topics include procedures and functions, iteration, recusion, arrays and vectors, strings, an operational model of procedure and function calls, algorithms, exceptions, object-oriented programming, and GUIs (graphical user interfaces). Weekly labs provide guided practice on the computer, with staff present to help. Assignments use graphics and GUIs to help develop fluency and understanding.
programming and problem solving using python emphasizes principles of software development style and testing topics include procedures and functions iteration recusion arrays and vectors strings an operational model of procedure and function calls algorithms exceptions objectoriented programming and guis graphical user interfaces weekly labs provide guided practice on the computer with staff present to help assignments use graphics and guis to help develop fluency and understanding
S

reading page: matlab
reading page: Multi-paradigm_programming_language
reading page: Multi-paradigm_programming_language
reading page: Numerical_analysis
reading page: Numerical_analysis
reading page: Proprietary_programming_language
reading page: Proprietary_programming_language
reading page: MathWorks
reading page: MathWorks
reading page: Matrix_(mathematics)
reading page: Matrix_(mathematics)
reading page: Function_(mathematics)
reading page: Function_(mathematics)
reading page: Algorithm
reading page: Algorithm
reading page: User_interface
reading page: User_interface
reading page: programming
reading page: programming
reading page: arithmetic
reading page: arithmetic
reading page: Ancient_Greek
reading page: Ancient_Greek
reading page: Number
reading page: Number
reading page: Art
reading page: Art
reading page: Mathematics
reading page: Mathematics
reading page: Operation_(mathematics)
reading page: Operation_(mathematics)
reading page: Addition
reading page: Addition
reading pag

reading page: matlab
reading page: Multi-paradigm_programming_language
reading page: Multi-paradigm_programming_language
reading page: Numerical_analysis
reading page: Numerical_analysis
reading page: Proprietary_programming_language
reading page: Proprietary_programming_language
reading page: MathWorks
reading page: MathWorks
reading page: Matrix_(mathematics)
reading page: Matrix_(mathematics)
reading page: Function_(mathematics)
reading page: Function_(mathematics)
reading page: Algorithm
reading page: Algorithm
reading page: User_interface
reading page: User_interface
reading page: programming
reading page: programming
reading page: conditionals
reading page: conditionals
reading page: vectorized
reading page: vectorized
reading page: constructs
reading page: constructs
reading page: iteration
reading page: iteration
reading page: Mathematics
reading page: Mathematics
reading page: arrays
reading page: arrays
reading page: assume
reading page: assume
reading page: graphics
reading 

reading page: python
reading page: programming
reading page: programming
reading page: vectorized
reading page: vectorized
reading page: conditionals
reading page: conditionals
reading page: constructs
reading page: constructs
reading page: iteration
reading page: iteration
reading page: Mathematics
reading page: Mathematics
reading page: arrays
reading page: arrays
reading page: assume
reading page: assume
reading page: objectoriented
reading page: objectoriented
reading page: computation
reading page: computation
reading page: Calculation
reading page: Calculation
reading page: Model_(abstract)
reading page: Model_(abstract)
reading page: Algorithm
reading page: Algorithm
({'/wiki/Model_(abstract)', '/wiki/computation', '/wiki/arrays', '/wiki/python', '/wiki/vectorized', '/wiki/Mathematics', '/wiki/iteration', '/wiki/Calculation', '/wiki/assume', '/wiki/Algorithm', '/wiki/programming', '/wiki/constructs', '/wiki/objectoriented', '/wiki/conditionals'}, ' Python may refer to:   Program

reading page: cs
reading page: description
reading page: description
reading page: Rhetorical_modes
reading page: Rhetorical_modes
reading page: fail
reading page: fail
reading page: Objective_(goal)
reading page: Objective_(goal)
reading page: Fracture
reading page: Fracture
reading page: Forensic_engineering
reading page: Forensic_engineering
reading page: Thomas_J._Watson
reading page: Thomas_J._Watson
reading page: fake
reading page: fake
({'/wiki/Rhetorical_modes', '/wiki/Forensic_engineering', '/wiki/fail', '/wiki/Thomas_J._Watson', '/wiki/cs', '/wiki/Objective_(goal)', '/wiki/fake', '/wiki/Fracture', '/wiki/description'}, ' CS, C-S, C.S., Cs, cs, or cs. may refer to:  Description is the pattern of narrative development that aims to make vivid a place, object, character, or group. Description is one of four rhetorical modes , along with exposition, argumentation, and narration.  In practice it would be difficult to write literature that drew on just one of the four basic modes. F

...

reading page: nlp
reading page: soon
reading page: soon
reading page: simply
reading page: simply
reading page: mandatory
reading page: mandatory
reading page: leads
reading page: leads
reading page: Typography
reading page: Typography
reading page: Help:IPA/English
reading page: Help:IPA/English
reading page: published
reading page: published
reading page: Dissemination
reading page: Dissemination
reading page: Literature
reading page: Literature
reading page: Music
reading page: Music
reading page: Information
reading page: Information
reading page: Content_(media_and_publishing)
reading page: Content_(media_and_publishing)
reading page: Media_(communication)
reading page: Media_(communication)
reading page: Imprint_(trade_name)
reading page: Imprint_(trade_name)
reading page: Newspaper
reading page: Newspaper
reading page: recently
reading page: recently
reading page: instead
reading page: instead
reading page: participant
reading page: participant
reading page: currently
reading pa

reading page: robotics
reading page: Interdisciplinarity
reading page: Interdisciplinarity
reading page: List_of_engineering_branches
reading page: List_of_engineering_branches
reading page: Branch_of_science
reading page: Branch_of_science
reading page: Mechanical_engineering
reading page: Mechanical_engineering
reading page: Electronic_engineering
reading page: Electronic_engineering
reading page: Information_engineering_(field)
reading page: Information_engineering_(field)
reading page: Computer_science
reading page: Computer_science
reading page: Robot
reading page: Robot
reading page: informal
reading page: informal
reading page: discussed
reading page: discussed
reading page: Deliberative_assembly
reading page: Deliberative_assembly
reading page: Conversation
reading page: Conversation
reading page: Discussion_moderator
reading page: Discussion_moderator
reading page: Debating_chamber
reading page: Debating_chamber
reading page: Voting
reading page: Voting
reading page: Wikipedia

reading page: cryptography
reading page: Ancient_Greek_language
reading page: Ancient_Greek_language
reading page: Romanization_of_Ancient_Greek
reading page: Romanization_of_Ancient_Greek
reading page: -logy
reading page: -logy
reading page: Secure_communication
reading page: Secure_communication
reading page: Adversary_(cryptography)
reading page: Adversary_(cryptography)
reading page: Communications_protocol
reading page: Communications_protocol
reading page: Information_security
reading page: Information_security
reading page: Confidentiality
reading page: Confidentiality
reading page: discussing
reading page: discussing
reading page: Deliberative_assembly
reading page: Deliberative_assembly
reading page: Conversation
reading page: Conversation
reading page: Discussion_moderator
reading page: Discussion_moderator
reading page: Debating_chamber
reading page: Debating_chamber
reading page: Voting
reading page: Voting
reading page: Wikipedia:Citation_needed
reading page: Wikipedia:Cit

reading page: cs
reading page: passed
reading page: passed
reading page: phd
reading page: phd
reading page: Latin
reading page: Latin
reading page: Thesis
reading page: Thesis
reading page: Professor
reading page: Professor
reading page: Research
reading page: Research
reading page: Doctor_(title)
reading page: Doctor_(title)
reading page: Post-nominal_letters
reading page: Post-nominal_letters
reading page: Doctorate
reading page: Doctorate
reading page: Comprehensive_examination
reading page: Comprehensive_examination
reading page: independent
reading page: independent
reading page: research
reading page: research
reading page: Creativity
reading page: Creativity
reading page: Knowledge
reading page: Knowledge
reading page: Theorem
reading page: Theorem
reading page: Theory
reading page: Theory
reading page: Basic_research
reading page: Basic_research
reading page: Applied_research
reading page: Applied_research
reading page: Documentation
reading page: Documentation
reading page: D

reading page: doctoral
reading page: Latin
reading page: Latin
reading page: Academic_degree
reading page: Academic_degree
reading page: Profession
reading page: Profession
reading page: Doctor_of_Philosophy
reading page: Doctor_of_Philosophy
reading page: Humanities
reading page: Humanities
reading page: Science
reading page: Science
reading page: Professional_degree
reading page: Professional_degree
reading page: Honorary_doctorate
reading page: Honorary_doctorate
reading page: research
reading page: research
reading page: Creativity
reading page: Creativity
reading page: Knowledge
reading page: Knowledge
reading page: Theorem
reading page: Theorem
reading page: Theory
reading page: Theory
reading page: Basic_research
reading page: Basic_research
reading page: Applied_research
reading page: Applied_research
reading page: Documentation
reading page: Documentation
reading page: Discovery_(observation)
reading page: Discovery_(observation)
({'/wiki/research', '/wiki/Knowledge', '/wiki/D

In [240]:
course_representations['CS 3410']

({'/wiki/Addition',
  '/wiki/Ancient_Greek',
  '/wiki/Arithmetic',
  '/wiki/Art',
  '/wiki/Boolean_algebra',
  '/wiki/Brain',
  '/wiki/Building',
  '/wiki/Computer_hardware',
  '/wiki/Computer_program',
  '/wiki/Computer_programming',
  '/wiki/Computer_science',
  '/wiki/Construction',
  '/wiki/Design',
  '/wiki/Foresight_(psychology)',
  '/wiki/Greek_language',
  '/wiki/Information',
  '/wiki/Information_processing',
  '/wiki/Latin',
  '/wiki/Marshall_McLuhan',
  '/wiki/Mathematics',
  '/wiki/Natural_science',
  '/wiki/Nicolas_L%C3%A9onard_Sadi_Carnot',
  '/wiki/Number',
  '/wiki/Operating_system',
  '/wiki/Operation_(mathematics)',
  '/wiki/Ordinary_(officer)',
  '/wiki/Organizational_theory',
  '/wiki/Personal_identity',
  '/wiki/Philosophy',
  '/wiki/Planning',
  '/wiki/Rudolf_Clausius',
  '/wiki/Sensory_processor',
  '/wiki/Sequence',
  '/wiki/Short-term_memory',
  '/wiki/Social_sciences',
  '/wiki/Software',
  '/wiki/Steam_engine',
  '/wiki/Structure',
  '/wiki/Subtraction',
  '/

In [233]:
pickle.dump( course_representations, open( "cs_representations.p", "wb" ) )

In [241]:
course_representations_simple = {}
for course_data in cornell_course_descriptions['CS']:
    course_number = course_data['courseNumber']
    course_desc = course_data['description']
    cleaned_course_desc = clean_text_for_vectorizer(course_desc)
    print(course_number)
    print(course_desc)
    print(cleaned_course_desc)
    top_tfidf_words = get_top_n_tfidf_terms_from_text(vectorizer, cleaned_course_desc, 5)
    print(top_tfidf_words)
    course_representation = generate_representation_for_course_description(top_tfidf_words, 0.10, 1, "")
    course_representations_simple['CS '+str(course_number)] = course_representation
    print(course_representation)
    print("************************")

1110
Programming and problem solving using Python. Emphasizes principles of software development, style, and testing. Topics include procedures and functions, iteration, recusion, arrays and vectors, strings, an operational model of procedure and function calls, algorithms, exceptions, object-oriented programming, and GUIs (graphical user interfaces). Weekly labs provide guided practice on the computer, with staff present to help. Assignments use graphics and GUIs to help develop fluency and understanding.
programming and problem solving using python emphasizes principles of software development style and testing topics include procedures and functions iteration recusion arrays and vectors strings an operational model of procedure and function calls algorithms exceptions objectoriented programming and guis graphical user interfaces weekly labs provide guided practice on the computer with staff present to help assignments use graphics and guis to help develop fluency and understanding
S

reading page: matlab
reading page: programming
reading page: programming
reading page: conditionals
reading page: conditionals
reading page: vectorized
reading page: vectorized
reading page: constructs
reading page: constructs
({'/wiki/programming', '/wiki/constructs', '/wiki/conditionals', '/wiki/vectorized', '/wiki/matlab'}, "  MATLAB  is a multi-paradigm numerical computing environment and proprietary programming language developed by MathWorks. MATLAB allows matrix manipulations, plotting of functions and data, implementation of algorithms, creation of user interfaces, and interfacing with programs written in other languages, including C, C++, C#, Java, Fortran and Python. Although MATLAB is intended primarily for numerical computing, an optional toolbox uses the MuPAD symbolic engine, allowing access to symbolic computing abilities. An additional package, Simulink, adds graphical multi-domain simulation and model-based design for dynamic and embedded systems. As of 2018, MATLAB ha

reading page: science
reading page: mind
reading page: mind
reading page: like
reading page: like
reading page: disciplines
reading page: disciplines
reading page: intities
reading page: intities
({'/wiki/disciplines', '/wiki/intities', '/wiki/science', '/wiki/mind', '/wiki/like'}, '   Science  is a systematic enterprise that builds and organizes knowledge in the form of testable explanations and predictions about the universe. The earliest roots of science can be traced to Ancient Egypt and Mesopotamia in around 3500 to 3000 BCE. Their contributions to mathematics, astronomy, and medicine entered and shaped Greek natural philosophy of classical antiquity, whereby formal attempts were made to explain events of the physical world based on natural causes. After the fall of the Western Roman Empire, knowledge of Greek conceptions of the world deteriorated in Western Europe during the early centuries  of the Middle Ages but was preserved in the Muslim world during the Islamic Golden Age. T

reading page: shell
reading page: computational
reading page: computational
reading page: files
reading page: files
reading page: installations
reading page: installations
reading page: strings
reading page: strings
({'/wiki/shell', '/wiki/computational', '/wiki/installations', '/wiki/strings', '/wiki/files'}, ' Shell may refer to:  Computation is any type of calculation that includes both arithmetical and non-arithmetical steps and follows a well-defined model, for example an algorithm. The study of computation is paramount to the discipline of computer science. A computation can be seen as a purely physical phenomenon occurring inside a closed physical system called a computer.Examples of such physical systems include digital computers, mechanical computers, quantum computers, DNA computers, molecular computers, microfluidics-based computers, analog computers, or wetware computers.This point of view has been adopted by the physics of computation, a branch of theoretical physics, as w

reading page: php
reading page: database
reading page: database
reading page: client
reading page: client
reading page: web
reading page: web
reading page: creation
reading page: creation
({'/wiki/web', '/wiki/client', '/wiki/php', '/wiki/creation', '/wiki/database'}, '  since version 7.0: PHP: Hypertext Preprocessor  is a general-purpose programming language originally designed for web development. It was originally created by Rasmus Lerdorf in 1994; the PHP reference implementation is now produced by The PHP Group. PHP originally stood for Personal Home Page, but it now stands for the recursive initialism PHP: Hypertext Preprocessor. PHP code may be executed with a command line interface , embedded into HTML code, or it can be used in combination with various web template systems, web content management systems, and web frameworks. PHP code is usually processed by a PHP interpreter implemented as a module in a web server or as a Common Gateway Interface  executable. The web server co

...

reading page: graphics
reading page: vision
reading page: vision
reading page: computer
reading page: computer
reading page: research
reading page: research
reading page: foster
reading page: foster
({'/wiki/computer', '/wiki/graphics', '/wiki/research', '/wiki/vision', '/wiki/foster'}, ' Graphics  are visual images or designs on some surface, such as a wall, canvas, screen, paper, or stone to inform, illustrate, or entertain. In contemporary usage, it includes a pictorial representation of data, as in computer-aided design and manufacture, in typesetting and the graphic arts, and in educational and recreational software. Images that are generated by a computer are called computer graphics. Examples are photographs, drawings, Line art, graphs, diagrams, typography, numbers, symbols, geometric designs, maps, engineering drawings,or other images. Graphics often combine text, illustration, and color. Graphic design may consist of the deliberate selection, creation, or arrangement of typog

reading page: ai
reading page: workinprogress
reading page: workinprogress
reading page: emphasizing
reading page: emphasizing
reading page: researchers
reading page: researchers
reading page: results
reading page: results
({'/wiki/workinprogress', '/wiki/researchers', '/wiki/results', '/wiki/emphasizing', '/wiki/ai'}, ' AI, A.I., Ai, or ai may refer to:  Other reasons this message may be displayed:  Other reasons this message may be displayed:   Research comprises "creative and systematic work undertaken to increase the stock of knowledge, including knowledge of humans, culture and society, and the use of this stock of knowledge to devise new applications." It is used to establish or confirm facts, reaffirm the results of previous work, solve new or existing problems, support theorems, or develop new theories. A research project may also be an expansion on past work in the field. Research projects can be used to develop further knowledge on a topic, or in the example of a school resea

reading page: nlp
reading page: soon
reading page: soon
reading page: simply
reading page: simply
reading page: mandatory
reading page: mandatory
reading page: leads
reading page: leads
({'/wiki/nlp', '/wiki/soon', '/wiki/mandatory', '/wiki/simply', '/wiki/leads'}, ' NLP may refer to:  Soon may refer to:  Simply may refer to:  Mandate may refer to:  In typography, leading  refers to the distance between adjacent lines of type; however, the exact definition has become confused. In the days of hand-typesetting, it referred to the thin strips of lead that were inserted into the forms to increase the vertical distance between lines of type; in this case, the leading would be defined as the difference between 2 quantities: the size of the type and the distance from one baseline to the next. For instance, given a type size of 10\xa0points and a distance between baselines of 12\xa0points, the leading would be 2\xa0points; put another way, a leading of 2\xa0points means there is a distance of 

reading page: cryptography
reading page: discussing
reading page: discussing
reading page: classical
reading page: classical
reading page: papers
reading page: papers
reading page: recent
reading page: recent
({'/wiki/discussing', '/wiki/classical', '/wiki/recent', '/wiki/cryptography', '/wiki/papers'}, '  Cryptography or cryptology ) is the practice and study of techniques for secure communication in the presence of third parties called adversaries. More generally, cryptography is about constructing and analyzing protocols that prevent third parties or the public from reading private messages; various aspects in information security such as data confidentiality, data integrity, authentication, and non-repudiation are central to modern cryptography. Modern cryptography exists at the intersection of the disciplines of mathematics, computer science, electrical engineering, communication science, and physics. Applications of cryptography include electronic commerce, chip-based payment car

reading page: doctoral
reading page: research
reading page: research
({'/wiki/research', '/wiki/doctoral'}, ' A doctorate  or doctor\'s degree  or doctoral degree, is an academic degree awarded by universities, derived from the ancient formalism licentia docendi   In most countries, it is a research degree that qualifies the holder to teach at university level in the degree\'s field, or to work in a specific profession. There are a variety of names for doctoral degrees; the most common is the Doctor of Philosophy , which is awarded in many different fields, ranging from the humanities to scientific disciplines. In the United States and some other countries, there are also some types of vocational, technical, or professional degrees that are referred to as doctorates. Professional doctorates historically came about to meet the needs of practitioners in a variety of disciplines. However, the necessity of these degrees may vary greatly across disciplines, making their significance unclear

In [242]:
pickle.dump( course_representations_simple, open( "cs_representations_simple.p", "wb" ) )